In [1]:
import requests
import re
import time

import pandas as pd
import lxml
from bs4 import BeautifulSoup
from unicodedata import normalize
from geopy.geocoders import Nominatim
from haversine import haversine
#import matplotlib.pyplot as plt
import numpy as np
from openpyxl import load_workbook
import xlsxwriter
import descartes
#from shapely.geometry import Point, Polygon
# Import necessary packages
import os 
import folium
from folium import plugins
import geopandas as gpd
#import rasterio as rio
#from rasterio.warp import calculate_default_transform, reproject, Resampling
import earthpy as et
from folium.plugins import MarkerCluster, HeatMap
from folium.plugins import FastMarkerCluster,FeatureGroupSubGroup
from folium import Popup
from flask import Flask
pd.options.display.max_rows = 4000
import IPython
from IPython.display import HTML, display
import panel as pn
import math
#import fiona
import json
from collections import Counter
import geojson
import us
import branca.colormap as cm
import datetime as dt

%matplotlib inline


In [2]:
df =  pd.read_csv("searchfund_allV6.csv")

In [5]:
cs_df = pd.read_csv("HeatCSV.csv")
#cs_df.drop(cs_df.loc[cs_df['Country']!='United States'].index, inplace=True)
#cs_df = cs_df.dropna()
#cs_df["County"] = cs_df['County'].str.replace(' County','')
fips = us.states.mapping('fips', 'name')
fips_2 = us.states.mapping('name', 'fips')
#cs_df['STATEFP'] = cs_df['State'].map(fips_2)
#counting the occurences of a county in the dataframe, one count stands for one searcher in the county
count_series = cs_df.groupby(['County', 'STATEFP', 'Country']).size()
count_series = count_series.to_frame(name = 'Searchers').reset_index()
gdf = gpd.read_file('counties.geojson')
gdf = gdf.rename(columns = {'NAME':'County'})
new_df = pd.merge(gdf, count_series,  how='left', left_on=['STATEFP','County'], right_on = ['STATEFP','County'])
new_df['State'] = new_df['STATEFP'].map(fips)
new_df["Searchers"] = new_df["Searchers"].fillna(0)
new_df["geometry"] = new_df["geometry"].simplify(tolerance = 0.9)
#new_df = new_df.simplify(tolerance = 0.5)

county_json = new_df.to_json()

KeyError: 'STATEFP'

In [15]:
df.groupby(['stage']).size()

stage
Acquired    631
Explore     224
Inactive    178
Raise       141
Search      779
dtype: int64

In [27]:
df.head()

Unnamed: 0                                               name  \
0           0                                     Nova Capital     
1           1  Galena Corp  Harvard University - Harvard Busi...   
2           2                                     Hanover West     
3           3  David Dodson - 1st Fund  Stanford University -...   
4           4                   Balkin Corp  Stanford University   

             type      formed                  Search Location     stage  \
0  Single Sponsor  1984-01-01        Boston, MA, United States  Acquired   
1     Traditional  1985-06-01     Palo Alto, CA, United States  Acquired   
2     Traditional  1986-01-01    Washington, DC, United States  Acquired   
3     Traditional  1987-06-01      Stanford, CA, United States  Acquired   
4     Traditional  1991-01-01  Redwood City, CA, United States  Acquired   

                       company    acquired  Searchfund Index searchWebsite  \
0             Uniform Printing  1984-01-01               420           NaN   
1          Alta Colleges, Inc.  1987-06-01               496           NaN   
2  Atlas Container Corporation  1988-11-01               501           NaN   
3          Smith Alarm Systems  1989-01-01               418           NaN   
4        Western Cable Systems  1991-01-01               430           NaN   

   ...               Acquistion Location  \
0  ...     Fort Worth, TX, United States   
1  ...         Denver, CO, United States   
2  ...         Severn, MD, United States   
3  ...                               NaN   
4  ...  San Francisco, CA, United States   

                               searchers  \
0                         'Jim Southern'   
1      'Jamie Turner ', 'Kirk Riedinger'   
2  'Paul Centenari ', 'Peter Centenari '   
3                         'David Dodson'   
4                         'Jeff Stevens'   

                                    investors associates Search Length  \
0                             'Irv Grousbeck'        NaN           0.0   
1                              'Rob Johnson '        NaN         730.0   
2                                         NaN        NaN        1035.0   
3  'Bill Egan ', 'Mark Egan ', 'Jim Southern'        NaN         580.0   
4                                         NaN        NaN           0.0   

  search long  search lat  acquisition lat  acquisition long  \
0  -71.058291   42.360253        32.753177        -97.332746   
1 -122.159847   37.444329        39.739236       -104.984862   
2  -77.036558   38.894992        39.127886        -76.686913   
3 -122.170293   37.426541              NaN               NaN   
4 -122.232523   37.486324        37.779026       -122.419906   

   Miles Between Search and Acquisiton  
0                          1576.275405  
1                           939.458691  
2                            24.724446  
3                                  NaN  
4                            22.674433  

[5 rows x 22 columns]

In [18]:
cs_df.head()

1936

In [61]:
geolocator = Nominatim(user_agent = "geoapiexercise")

t_latitude = str(df.iloc[2]['search lat'])
t_longitude = str(df.iloc[2]['search long'])
t_name = df.iloc[1]['name']
t_stage = df.iloc[1]['stage']
t_location = geolocator.reverse(t_latitude + "," + t_longitude)
t_address = t_location.raw['address']
    
t_state = t_address.get('state')
t_country = t_address.get('country')
t_county = t_address.get('county')


In [62]:
t_address

{'historic': 'Zero Milestone',
 'road': 'Ellipse Road Northwest',
 'city': 'Washington',
 'state': 'District of Columbia',
 'postcode': '20500',
 'country': 'United States',
 'country_code': 'us'}

In [35]:
#geolocating for the searchers
#using nominatim to geocode the location of each searcher based on the latitude and longitude
geolocator = Nominatim(user_agent = "geoapiexercise")
searching_states = []
searching_country = []
searching_county = []
lat_list = []
long_list = []
name_list = []
stage_list = []
for i in range(df.shape[0]):
    try:
        latitude = str(df.iloc[i]['search lat'])
        longitude = str(df.iloc[i]['search long'])
        name = df.iloc[i]['name']
        stage = df.iloc[i]['stage']
        location = geolocator.reverse(latitude + "," + longitude)
    
        address = location.raw['address']
    
        searching_county   
        state = address.get('state')
        country = address.get('country')
        county = address.get('county')
    
        name_list.append(name)
        stage_list.append(stage)
        lat_list.append(latitude)
        long_list.append(longitude)
        searching_states.append(state)  
        searching_country.append(country)
        searching_county.append(county)
    except ValueError:
        print("ValueError")

ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError
ValueError


Counter({'Suffolk County': 103,
         'Santa Clara County': 35,
         None: 450,
         'San Mateo County': 16,
         'San Francisco': 68,
         'Salt Lake County': 18,
         'Tarrant County': 11,
         'Galveston County': 2,
         'Contra Costa County': 1,
         'King County': 28,
         'New York County': 156,
         'Kent County': 2,
         'Polk County': 6,
         'Sonoma County': 2,
         'Snohomish County': 3,
         'Lane County': 1,
         'Orange County': 15,
         'Provincia de Choapa': 2,
         'Lake County': 44,
         'Hartford County': 7,
         'Worcester County': 2,
         'Clackamas County': 1,
         'Bernalillo County': 1,
         'Hamilton County': 6,
         'Dallas County': 53,
         'Travis County': 43,
         'Hennepin County': 16,
         'York Region': 2,
         'Manitowoc County': 1,
         'Cook County': 71,
         'Allegheny County': 22,
         'Fulton County': 53,
         'Lee County':

In [45]:
#counting the amount of searchers in each us state and each us county
state_list = Counter(searching_states)
county_list = Counter(searching_county)
#zipping together the county, searching state, and country for each searchfund listed in the database
state_county = list(zip(name_list, searching_county, searching_states, searching_country, stage_list, lat_list, long_list))
#creating a dataframe that contains the county, state and country for each searcher. Then cleaning the data
cs_df = pd.DataFrame(state_county, columns = ["Name", "County", "State", "Country", "Stage", "Latitude", "Longitude"])
#cs_df.to_csv("county_location.csv")

In [263]:
cs_df.to_csv("county_location.csv")

In [63]:
gdf = gpd.read_file('counties.geojson')
gdf = gdf.rename(columns = {'NAME':'County'})

In [65]:
cs_df.drop(cs_df.loc[cs_df['Country']!='United States'].index, inplace=True)
cs_df = cs_df.dropna()
cs_df["County"] = cs_df['County'].str.replace(' County','')

C:\Users\PATRIC~1\AppData\Local\Temp/ipykernel_14748/67141308.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cs_df["County"] = cs_df['County'].str.replace(' County','')


In [67]:
cs_df['STATEFP'] = cs_df['State'].map(fips_2)

C:\Users\PATRIC~1\AppData\Local\Temp/ipykernel_14748/2090237130.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cs_df['STATEFP'] = cs_df['State'].map(fips_2)


In [174]:
cs_df

Name  \
0                                        Nova Capital     
1     Galena Corp  Harvard University - Harvard Busi...   
3     David Dodson - 1st Fund  Stanford University -...   
4                      Balkin Corp  Stanford University   
5                                     Braden Partners     
6                               Sverica International     
10                                Falcon Capital Corp.    
11                              Mill River Corporation    
12                             Gene Baker Search Fund     
13                                Sansair Corporation     
15                                    The Nexus Group     
16                                      Russell Poore     
17                                  Presidio Partners     
18                         Jim Southern Search Fund 2     
19                                      Ancora Capital    
20                                Gulf Search Capital     
21                            Al Kapoor - Search Fund     
22                                      Gregory Mazur     
23    First American Records Management Company (FAR...   
24                   Circle Point Capital Corporation     
25                         Tony Distefano Search Fund     
26                                         Falck Holt     
27                                    Rockwood Equity     
28    Blackford Capital  Harvard University - Harvar...   
29                                 Mike and Linda Katz    
30                         Jim Southern Search Fund 3     
32          Pratap Mukherjee & Brian Haas Serach Fund     
33                       Michael Sanabria Search Fund     
34                                        SC Ventures     
35                                 Montebello Capital     
36                                   Teton Industries     
38                       Crystal Springs Capital, LLC     
40                                             Julie Ha   
41                              Leader Creek Partners     
42                                     Dionis Company     
43              Eventide Management  Colgate University   
44                                AP Capital Partners     
45                         Rabbit Creek Partners, LLC     
46                                         Access CIG     
47                           Liffey Thames Group, LLC     
49             Argo Investors LLC  Princeton University   
50                           Argo Management Partners     
52                       A.J. Wasserstein Search Fund     
54                            Jim Edmunds search fund     
55                                  Wheelock Partners     
56                                  Headland Partners     
57                                Willow Capital, LLC     
58                               Entrada Ventures LLC     
59                              Stoddard Hill Capital     
60                                Footbridge Partners     
62                                VantageCap Partners     
63                                Mt. Auburn Partners     
64                              Council Oak Investors     
65                       North Point Capital Partners     
67                                  Fairview Partners     
68                                   Scout Capital LLC    
69                                   Reticle Partners     
70                              J. Devien Capital LLC     
71                               Diligent Capital LLC     
73                          Travis Ayers' Search Fund     
74                            Buck Creek Capital, LLC     
75                                Blue Canyon Capital     
76                           Geminus Capital Partners     
79                               Johns Creek Partners     
81                                Pinamar Investments     
82                         HWI Partners - Search Fund I   
83                                     Gordian Capital    
85                          Sean Callah

In [235]:
stage = cs_df.groupby(['Stage','County', 'STATEFP'], as_index = False).size().pivot(["County", "STATEFP"], ["Stage"]).fillna(0)
stage = stage.reset_index()

size                              
Stage             Acquired Explore Inactive Raise Search
County    STATEFP                                       
Ada       16           0.0     1.0      0.0   0.0    1.0
Adams     08           0.0     1.0      0.0   0.0    0.0
Alameda   06           3.0     1.0      0.0   0.0    3.0
Allegheny 42           6.0     1.0      5.0   0.0   10.0
Allen     18           0.0     0.0      0.0   0.0    1.0

County STATEFP     size                              
Stage                    Acquired Explore Inactive Raise Search
0            Ada      16      0.0     1.0      0.0   0.0    1.0
1          Adams      08      0.0     1.0      0.0   0.0    0.0
2        Alameda      06      3.0     1.0      0.0   0.0    3.0
3      Allegheny      42      6.0     1.0      5.0   0.0   10.0
4          Allen      18      0.0     0.0      0.0   0.0    1.0

In [253]:
stage_df = pd.merge(gdf, stage,  how='left', left_on=['STATEFP','County'], right_on = ['STATEFP','County']).fillna(0)
stage_df = stage_df.rename(columns={('size', 'Acquired'): "Acquired", ('size', 'Explore'): "Explore", ('size', 'Inactive'): "Inactive", ('size', 'Raise'): 'Raise', ('size', 'Search'): 'Search'})

C:\Users\PATRIC~1\AppData\Local\Temp/ipykernel_14748/3787564703.py:1: FutureWarning: merging between different levels is deprecated and will be removed in a future version. (1 levels on the left,2 on the right)
  stage_df = pd.merge(gdf, stage,  how='left', left_on=['STATEFP','County'], right_on = ['STATEFP','County']).fillna(0)
c:\users\patrick moore\appdata\local\programs\python\python39\lib\site-packages\pandas\core\generic.py:4147: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  obj = obj._drop_axis(labels, axis, level=level, errors=errors)


In [254]:
stage_df.head()

STATEFP COUNTYFP  COUNTYNS        AFFGEOID  GEOID         County LSAD  \
0      06      075  00277302  0500000US06075  06075  San Francisco   06   
1      25      025  00606939  0500000US25025  25025        Suffolk   06   
2      31      007  00835826  0500000US31007  31007         Banner   06   
3      37      181  01008591  0500000US37181  37181          Vance   06   
4      48      421  01383996  0500000US48421  48421        Sherman   06   

        ALAND     AWATER                                           geometry  \
0   121485107  479107241  POLYGON ((-122.51198 37.77113, -122.46540 37.8...   
1   150855462  160479920  POLYGON ((-71.19115 42.28306, -71.15689 42.330...   
2  1932676697     397069  POLYGON ((-104.05283 41.69795, -103.37039 41.6...   
3   653705784   42187365  POLYGON ((-78.49778 36.51448, -78.45728 36.541...   
4  2390651189     428754  POLYGON ((-102.16246 36.50033, -102.03234 36.5...   

   Acquired  Explore  Inactive  Raise  Search  
0      30.0      4.0      16.0    2.0    16.0  
1      46.0      9.0      12.0    3.0    32.0  
2       0.0      0.0       0.0    0.0     0.0  
3       0.0      0.0       0.0    0.0     0.0  
4       0.0      0.0       0.0    0.0     0.0

In [255]:
county_json = stage_df.to_json()

In [259]:
county_map = folium.Map(location=[48,-102], zoom_start = 2, title = "mapbox")

In [260]:
county_colormap = cm.LinearColormap(["cyan", "blue", "darkblue"], vmin = 1, vmax = stage_df["Search"].max())
county_colormap.caption = "Searchers Per County"
style_function = lambda x: {"weight":0.5, 
                            'color': "black",
                            'fillColor':county_colormap(x['properties']['Search']) if 0 < x['properties']['Search'] else '#00000000',
                            'fillOpacity':0.75}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}
county=folium.features.GeoJson(
        data = county_json,
        style_function=style_function,
        name = "County Hover Tool",
        control=True,
        overlay = True,
        show = False,
        highlight_function=highlight_function,
        tooltip=folium.features.GeoJsonTooltip(
            fields=['County','Search', 'Explore', 'Raise', 'Acquired', 'Inactive'],
            aliases=['County: ','Currently Searching: ', 'Currently Exploring: ', 'Currently Raising: ', 'Acquired: ', 'Inactive: '],
            style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;"),
            sticky=True
        )
    )
county_colormap.add_to(county_map)
county_map.add_child(county)

In [261]:
stage_df.to_csv("County_Searchers.csv")

In [264]:
stage_df

STATEFP COUNTYFP  COUNTYNS        AFFGEOID  GEOID                 County  \
0         06      075  00277302  0500000US06075  06075          San Francisco   
1         25      025  00606939  0500000US25025  25025                Suffolk   
2         31      007  00835826  0500000US31007  31007                 Banner   
3         37      181  01008591  0500000US37181  37181                  Vance   
4         48      421  01383996  0500000US48421  48421                Sherman   
5         50      011  01461762  0500000US50011  50011               Franklin   
6         51      680  01498429  0500000US51680  51680              Lynchburg   
7         05      099  00069169  0500000US05099  05099                 Nevada   
8         08      014  01945881  0500000US08014  08014             Broomfield   
9         16      065  00394803  0500000US16065  16065                Madison   
10        17      027  00424215  0500000US17027  17027                Clinton   
11        19      025  00465202  0500000US19025  19025                Calhoun   
12        21      129  00516911  0500000US21129  21129                    Lee   
13        22      063  00558083  0500000US22063  22063             Livingston   
14        31      097  00835870  0500000US31097  31097                Johnson   
15        31      101  00835872  0500000US31101  31101                  Keith   
16        51      775  01789074  0500000US51775  51775                  Salem   
17        48      493  01384032  0500000US48493  48493                 Wilson   
18        48      115  01383843  0500000US48115  48115                 Dawson   
19        46      051  01265782  0500000US46051  46051                  Grant   
20        72      101  01804531  0500000US72101  72101                Morovis   
21        05      067  00066861  0500000US05067  05067                Jackson   
22        51      670  01498428  0500000US51670  51670               Hopewell   
23        46      003  01266983  0500000US46003  46003                 Aurora   
24        18      031  00450345  0500000US18031  18031                Decatur   
25        18      169  00450399  0500000US18169  18169                 Wabash   
26        19      161  00465269  0500000US19161  19161                    Sac   
27        37      107  01008568  0500000US37107  37107                 Lenoir   
28        29      055  00758482  0500000US29055  29055               Crawford   
29        31      105  00835874  0500000US31105  31105                Kimball   
30        08      045  00198138  0500000US08045  08045               Garfield   
31        17      067  00424235  0500000US17067  17067                Hancock   
32        27      173  00659531  0500000US27173  27173        Yellow Medicine   
33        31      145  00835894  0500000US31145  31145             Red Willow   
34        13      089  01687424  0500000US13089  13089                 DeKalb   
35        45      077  01248015  0500000US45077  45077                Pickens   
36        20      131  00485029  0500000US20131  20131                 Nemaha   
37        05      111  00069174  0500000US05111  05111               Poinsett   
38        17      175  00424288  0500000US17175  17175                  Stark   
39        37      147  01008578  0500000US37147  37147                   Pitt   
40        19      147  00465262  0500000US19147  19147              Palo Alto   
41        19      081  00465229  0500000US19081  19081                Hancock   
42        29      229  00758567  0500000US29229  29229                 Wright   
43        31      073  00835858  0500000US31073  31073                 Gosper   
44        38      043  01034206  0500000US38043  38043                 Kidder   
45        40      015  01101795  0500000US40015  40015                  Caddo   
46        42      075  01214034  0500000US42075  42075                Lebanon   
47        48      069  01383820  0500000US48069  48069                 Castro   
48        48      279  01383926  050

County STATEFP        Country  Searchers
0                        Ada      16  United States          2
1                      Adams      08  United States          1
2                    Alameda      06  United States          7
3                  Allegheny      42  United States         22
4                      Allen      18  United States          1
5                   Arapahoe      08  United States          1
6                  Arlington      51  United States          1
7                   Atlantic      34  United States          1
8                     Bergen      34  United States          1
9                      Berks      42  United States          1
10                Bernalillo      35  United States          1
11                     Bexar      48  United States          4
12                    Blaine      16  United States          1
13                     Boone      18  United States          1
14                   Boulder      08  United States          1
15                   Brevard      12  United States          1
16                   Bristol      51  United States          1
17                   Broward      12  United States          2
18                  Burleson      48  United States          1
19                  Cabarrus      37  United States          1
20                     Cache      49  United States          1
21                    Camden      34  United States          1
22                   Carroll      24  United States          2
23                  Carteret      37  United States          2
24                    Centre      42  United States          3
25                   Chaffee      08  United States          1
26                 Champaign      17  United States          1
27                Charleston      45  United States          3
28                   Chatham      13  United States          1
29                   Chatham      37  United States          4
30                Chittenden      50  United States          3
31                   Choctaw      01  United States          1
32                 Clackamas      41  United States          1
33                     Clark      32  United States          2
34                     Clark      53  United States          3
35                   Coleman      48  United States          2
36                   Collier      12  United States          1
37                    Collin      48  United States          3
38              Contra Costa      06  United States          1
39                      Cook      17  United States         71
40                Cumberland      23  United States          4
41                  Cuyahoga      39  United States          8
42                    Dallas      48  United States         53
43                      Dare      37  United States          1
44                  Davidson      37  United States          1
45                  Davidson      47  United States          8
46                     Davis      49  United States          2
47                   Decatur      20  United States          4
48                  Delaware      42  United States          1
49                    Denver      08  United States         26
50                   Douglas      31  United States          2
51                   Douglas      32  United States          1
52                    DuPage      17  United States          3
53                    Durham      37  United States          8
54                  Dutchess      36  United States          1
55                     Duval      12  United States          2
56   East Baton Rouge Parish      22  United States          1
57                 Edgecombe      37  United States          1
58                      Erie      36  United States          1
59                  Escambia      12  United States          1
60                   Fairfax      51  United States          1
61                 Fairfield      09  United States          5
62                  Faulkner      05  United States  